# Mumbai and Delhi similarity Clustering

In [1]:
import numpy as np

import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json 

#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


### Web Scrapping for Mumbai neighborhood data fetching

In [11]:
table_m = pd.read_html("https://www.mapsofindia.com/pincode/india/maharashtra/mumbai/",header=0,index_col=0)
Borough = ['Mumbai']

In [12]:
mumbai = table_m[0]
mumbai = mumbai.reset_index()
mumbai.rename(columns = {'Pincode Details':'Neighborhood','Pincode Details.1':'Pincode','Pincode Details.2': 'State','Pincode Details.3': 'District'}, inplace = True)    
mumbai=mumbai.drop(columns=[ 'State'])
mumbai=mumbai.drop(mumbai.index[0])
mumbai.head()

Neighborhood Pincode District
1  A I staff colony  400029   Mumbai
2  Aareymilk Colony  400065   Mumbai
3          Agripada  400011   Mumbai
4           Airport  400099   Mumbai
5          Ambewadi  400004   Mumbai

### Nominatim function to obtain Geo cordinates for respective nighborhoods

In [13]:
# define a sample to get coordinates
locator = Nominatim(user_agent='myGeocoder')
location = locator.geocode('Borivali', 'Mumbai')
print('latitude = {}, longitude = {}'.format(location.latitude, location.longitude))

latitude = 19.229068, longitude = 72.8573628


In [14]:
# define a function to get coordinates
def get_latlng(Neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    lat_lng_coords = locator.geocode(Neighborhood)
    
    if(lat_lng_coords is None):
        for i in range(5):
            lat_lng_coords = locator.geocode(Neighborhood)
    if(lat_lng_coords is None):
        lat_lng_coords = 'Nan'
    return lat_lng_coords

In [15]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng('{},Mumbai'.format(Neighborhood)) for Neighborhood in mumbai["Neighborhood"].tolist() ]
coords

['Nan',
 'Nan',
 Location(Agripada, Zone 1, Mumbai, Mumbai City, Maharashtra, 400034, India, (18.9753024, 72.8248975, 0.0)),
 Location(Chhatrapati Shivaji International Airport, Sahar Elevated Road, Sahar Gaon, K/E Ward, Zone 3, Mumbai, Mumbai Suburban, Maharashtra, 400 059, India, (19.0902005, 72.86380844765398, 0.0)),
 Location(Ambewadi, Zone 4, Mumbai, Mumbai Suburban, Maharashtra, 400097, India, (19.1867764, 72.8593129, 0.0)),
 Location(Andheri, Madhavdas Amarshi Marg, K/W Ward, Zone 3, Mumbai, Mumbai Suburban, Maharashtra, 400058, India, (19.1196976, 72.8464205, 0.0)),
 Location(Andheri East, Zone 3, Mumbai, Mumbai Suburban, Maharashtra, 400 099, India, (19.1158835, 72.854202, 0.0)),
 Location(Andheri, Madhavdas Amarshi Marg, K/W Ward, Zone 3, Mumbai, Mumbai Suburban, Maharashtra, 400058, India, (19.1196976, 72.8464205, 0.0)),
 Location(Antop Hill, Mumbai, Mumbai City, Maharashtra, 400037, India, (19.0207608, 72.8652556, 0.0)),
 Location(INHS Asvini, Nanabhai Moos Marg, Dhobi Ghat

In [16]:
latitude = []
longitude = []
for data in coords:
    if data != 'Nan':
        latitude.append(data.latitude)
        longitude.append(data.longitude)
    else :
        latitude.append(0)
        longitude.append(0)

In [17]:
mumbai['Latitude']=latitude
mumbai['Longitude']=longitude
mumbai = mumbai[mumbai['Latitude'] != 0]
mumbai.head()

Neighborhood Pincode District   Latitude  Longitude
3      Agripada  400011   Mumbai  18.975302  72.824898
4       Airport  400099   Mumbai  19.090201  72.863808
5      Ambewadi  400004   Mumbai  19.186776  72.859313
6       Andheri  400053   Mumbai  19.119698  72.846420
7  Andheri East  400069   Mumbai  19.115883  72.854202

### Web Scrapping for Mumbai neighborhood data fetching¶

In [18]:
tables_d = pd.read_html("https://www.movingsolutions.in/blog/2020/02/05/pin-codes-of-delhi-locations/",header=0,index_col=0)
Borough_d = ['East Delhi', 'West delhi', 'South Delhi', 'North Delhi', 'New Delhi', 'Central Delhi', 'West Delhi', 'South West Delhi']

In [19]:
for i in range(len(Borough_d)):
    tables_d[i]['District']=Borough_d[i]  
Delhi = tables_d[0]    
for j in range(len(Borough_d)-1):
    Delhi = pd.concat([Delhi, tables_d[j+1]])

Delhi = Delhi.reset_index()
Delhi.rename(columns = {'Location':'Neighborhood', 'Pin code':'Pincode', 'District':'Borough'}, inplace = True)    
Delhi.head()

Neighborhood  Pincode     Borough
0   Anand Vihar   110092  East Delhi
1    Azad Nagar   110051  East Delhi
2      Babarpur   110032  East Delhi
3  Balbir Nagar   110032  East Delhi
4   Bhajan Pura   110053  East Delhi

### Nominatim function to obtain Geo cordinates for respective nighborhoods

In [20]:
location = locator.geocode('adarsh nagar,delhi, india')
print('Latitude = {}, Longitude = {}'.format(location.latitude, location.longitude))

Latitude = 28.7144008, Longitude = 77.1672884


In [21]:
# call the function to get the coordinates, store in a new list using list comprehension
coords_d = [ get_latlng('{}, Delhi, india'.format(Neighborhood)) for Neighborhood in Delhi["Neighborhood"].tolist() ]

In [22]:
latitude = []
longitude = []
for data in coords_d:
    if data != 'Nan':
        latitude.append(data.latitude)
        longitude.append(data.longitude)
    else :
        latitude.append(0)
        longitude.append(0)

In [23]:
Delhi['Latitude']=latitude
Delhi['Longitude']=longitude
Delhi.shape

(493, 5)

In [24]:
Delhi = Delhi[Delhi['Latitude'] != 0]
Delhi

Neighborhood  Pincode           Borough   Latitude  Longitude
0                Anand Vihar   110092        East Delhi  28.641115  77.312502
1                 Azad Nagar   110051        East Delhi  28.662682  77.279515
2                   Babarpur   110032        East Delhi  28.687431  77.279755
3               Balbir Nagar   110032        East Delhi  28.683790  77.290754
5           Bhola Nath nagar   110032        East Delhi  28.669127  77.285241
7                     Chilla   110091        East Delhi  28.595984  77.300936
9             Dilshad Garden   110095        East Delhi  28.675826  77.321516
11           G.T.B. Hospital   110095        East Delhi  28.684560  77.311077
12              Gandhi Nagar   110031        East Delhi  28.453175  77.015329
13        Gandhi Nagar bazar   110031        East Delhi  28.656097  77.235436
14              Geeta Colony   110031        East Delhi  28.650101  77.275921
15                  Ghazipur   110096        East Delhi  28.628183  77.325442
20                Himmatpuri   110091        East Delhi  28.603240  77.303379
21                  Jafrabad   110053        East Delhi  28.686733  77.276633
23                   Jhilmil   110095        East Delhi  28.675720  77.312395
24          Jhilmil Tahirpur   110095        East Delhi  28.687285  77.317890
25                  Johripur   110094        East Delhi  28.651718  77.221939
26             Kailash Nagar   110031        East Delhi  28.662608  77.258214
27                Kalyanpuri   110091        East Delhi  28.619491  77.317951
28                 Kalyanvas   110091        East Delhi  28.619907  77.310951
29             Karawal Nagar   110094        East Delhi  28.731141  77.274790
31             Krishna Nagar   110051        East Delhi  28.657846  77.290185
32               Laxmi Nagar   110092        East Delhi  28.630553  77.277575
33                 Loni Road   110032        East Delhi  28.749599  77.286643
36        Mandawali Fazalpur   110092        East Delhi  28.628009  77.288363
38                   Maujpur   110053        East Delhi  28.692078  77.279697
40          Mayur Vihar Ph 3   110096        East Delhi  28.613107  77.295722
41                Nand Nagri   110093        East Delhi  28.694458  77.316144
42             New Seemapuri   110095        East Delhi  28.686813  77.325333
43              New Usmanpur   110053        East Delhi  28.683855  77.256005
44              Nirman Vihar   110092        East Delhi  28.636493  77.286794
45             Old Seemapuri   110095        East Delhi  28.680655  77.328367
46                Patparganj   110091        East Delhi  28.611592  77.290564
49                 Ram Nagar   110051        East Delhi  28.648244  77.215412
52                 Seelampur   110053        East Delhi  28.669816  77.266814
53                  Shahdara   110032        East Delhi  28.673333  77.289025
55                 Shakarpur   110092        East Delhi  28.629489  77.281061
56             Shastri Nagar   110031        East Delhi  28.670088  77.181859
57              Shivaji Park   110032        East Delhi  28.675032  77.130472
58               Sonia Vihar   110094        East Delhi  28.719926  77.248182
59            Surajmal Vihar   110092        East Delhi  28.660807  77.307544
61                Trilokpuri   110091        East Delhi  28.605647  77.306648
62                V.K. Nagar   110095        East Delhi  28.619298  77.030036
64             Vishwas Nagar   110032        East Delhi  28.664436  77.294960
65               Vivek Vihar   110095        East Delhi  28.669164  77.312267
66              Yamuna Vihar   110053        East Delhi  28.700372  77.272773
68               Ashok Nagar   110018        West delhi  28.636021  77.101822
70                Bakkarwala   110015        West delhi  28.667065  77.019182
71               Chand Nagar   110018        West delhi  28.646991  77.097591
72                Chaukhandi   110015        West delhi  28.645138  77.096568
75     Delhi Industrial Area   110015 

## Merging Delhi and Mumbai dataframes

In [25]:
data=pd.concat([mumbai,Delhi], axis=0 )
data.drop(['Borough', 'District', 'Pincode'],axis=1,inplace=True)
data

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  if __name__ == '__main__':


Latitude   Longitude             Neighborhood
3    18.975302   72.824898                 Agripada
4    19.090201   72.863808                  Airport
5    19.186776   72.859313                 Ambewadi
6    19.119698   72.846420                  Andheri
7    19.115883   72.854202             Andheri East
8    19.119698   72.846420  Andheri Railway station
9    19.020761   72.865256               Antop Hill
10   18.900689   72.816134                   Asvini
11   19.128315   72.840038               Azad Nagar
12   19.101937   72.861599             B P t colony
13   18.941065   72.793917              B.N. bhavan
14    5.416873  100.340014                 B.P.lane
15   19.058336   72.830267              Bandra West
16   19.061657   72.849811             Bandra(east)
17   19.168814   72.833678             Bangur Nagar
18   18.928665   72.832264                Bazargate
19   19.152814   72.839021        Best Staff colony
20   19.063330   72.856474             Bharat Nagar
21   19.015786   72.837370          Bhawani Shankar
22   19.019009   72.840432       Bhawani Shankar rd
23   19.229068   72.857363                 Borivali
24   19.226723   72.861933            Borivali East
27   18.938771   72.835335         Central Building
28   19.009200   72.825565             Century Mill
29   19.115287   72.861808             Chakala Midc
30   19.001759   72.840800               Chamarbaug
31   19.214119   72.825865                  Charkop
32   18.952456   72.817440              Charni Road
34   18.956751   72.837053             Chinchbunder
35   18.987198   72.832672              Chinchpokli
36   18.935957   72.827340               Churchgate
37   18.915091   72.825969                   Colaba
38   18.987249   72.845762          Cotton Exchange
39   18.969307   72.806538            Cumballa Hill
41   19.019282   72.842876                    Dadar
42   19.023823   72.839427             Dadar Colony
43   19.249450   72.859621                  Dahisar
45   19.076779   72.825031                    Danda
46   19.236378   72.860493             Daulat Nagar
47   18.993260   72.831012             Delisle Road
48   19.044463   72.858618                  Dharavi
49   19.044463   72.858618             Dharavi Road
50   18.967477   72.844548            Dockyard Road
51   18.970337   72.809547         Dr Deshmukh marg
52   18.963963   72.820791            Falkland Road
53   18.954317   72.817908                  Girgaon
54   19.017067   72.835284             Gokhale Road
55   19.164753   72.850018                 Goregaon
56   19.169262   72.855255            Goregaon East
58   19.019274   72.832030        Government Colony
59   18.962095   72.810098             Gowalia Tank
60   18.964447   72.813573               Grant Road
63   18.972063   72.832289              Haines Road
65   18.948282   72.830243             Hanuman Road
68   19.120547   72.820843                     Irla
69   19.192673   72.797614                Ins Hamla
70   19.090201   72.863808    International Airport
71   18.938771   72.835335               J.B. nagar
72   18.963895   72.834717             J.J.hospital
73   18.981053   72.826786             Jacob Circle
74   19.136989   72.864942          Jogeshwari East
75   19.136394   72.837382          Jogeshwari West
76   19.107021   72.827528                     Juhu
78   18.949258   72.827938                Kalbadevi
79   18.965322   72.826435              Kamathipura
80   19.210381   72.864084           Kandivali East
81   19.208380   72.842227           Kandivali West
83   19.256092   72.874835                Ketkipada
86   19.191684   72.814098                  Kharodi
87   19.061218   72.844873                 Kherwadi
88   19.008436   72.852981             Kidwai Nagar
90   18.993529   72.842407                 Lal Baug
91   19.187832   72.841534           Liberty Garden
92   18.990978   73.065553                 M A marg
93    5.416873  100.340014                   M.P.t.
94   19.137528   72.791886                     Madh
95

### obtaining Geocodes of Mumbai for creating a map

In [26]:
address = 'Mumbai, IN'

location = locator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Mumbai are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Mumbai are 18.9387711, 72.8353355.


In [27]:
map = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for Latitude, Longitude,  Neighborhood in zip(data['Latitude'], data['Longitude'], data['Neighborhood']):
    label = '{}'.format(Neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [Latitude, Longitude],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map) 
    
map

In [28]:
# #hidden_cell
CLIENT_ID = 'WDYUDPBSNVHNSR3NNV54QXP4GSSMGFF0Z5XMRWFPEW2UFL3T' # your Foursquare ID
CLIENT_SECRET = 'YH0RSL4NX0PRPVCJPTCSHPNH3QCOBLPRZHGXKZ0YKPHAZQFS' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: WDYUDPBSNVHNSR3NNV54QXP4GSSMGFF0Z5XMRWFPEW2UFL3T
CLIENT_SECRET:YH0RSL4NX0PRPVCJPTCSHPNH3QCOBLPRZHGXKZ0YKPHAZQFS


In [29]:
#Let's get the geographical coordinates of Anand Vihar
neighborhood_latitude = data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Anand Vihar are 28.641115, 77.3125024.


In [30]:
LIMIT = 100
radius = 1000
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

In [31]:
results = requests.get(url).json()

In [32]:
#let's borrow the get_category_type function from the Foursquare lab. function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [33]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name     categories        lat        lng
0            PVR EDM  Movie Theater  28.641323  77.317026
1          Pizza Hut    Pizza Place  28.641347  77.317054
2    Barista Lavazza           Café  28.646416  77.320005
3  Big Cinemas, Imax      Multiplex  28.645940  77.319942
4   Lemon Tree Hotel          Hotel  28.641373  77.316549

In [34]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))


12 venues were returned by Foursquare.


In [35]:
def getNearbyVenues(names, latitudes, longitudes, radius=300):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [38]:
all_venues = getNearbyVenues(names=data['Neighborhood'],
                   latitudes=data['Latitude'],
                   longitudes=data['Longitude']
                 )

Agripada
Airport
Ambewadi
Andheri
Andheri East
Andheri Railway station
Antop Hill
Asvini
Azad Nagar
B P t colony
B.N. bhavan
B.P.lane
Bandra West
Bandra(east)
Bangur Nagar
Bazargate
Best Staff colony
Bharat Nagar
Bhawani Shankar
Bhawani Shankar rd
Borivali
Borivali East
Central Building
Century Mill
Chakala Midc
Chamarbaug
Charkop
Charni Road
Chinchbunder
Chinchpokli
Churchgate
Colaba
Cotton Exchange
Cumballa Hill
Dadar
Dadar Colony
Dahisar
Danda
Daulat Nagar
Delisle Road
Dharavi
Dharavi Road
Dockyard Road
Dr Deshmukh marg
Falkland Road
Girgaon
Gokhale Road
Goregaon
Goregaon East
Government Colony
Gowalia Tank
Grant Road
Haines Road
Hanuman Road
Irla
Ins Hamla
International Airport
J.B. nagar
J.J.hospital
Jacob Circle
Jogeshwari East
Jogeshwari West
Juhu
Kalbadevi
Kamathipura
Kandivali East
Kandivali West
Ketkipada
Kharodi
Kherwadi
Kidwai Nagar
Lal Baug
Liberty Garden
M A marg
M.P.t.
Madh
Madhavbaug
Mahim
Mahim East
Malabar Hill
Malad
Malad East
Mandapeshwar
Mandvi
Mantralaya
Marine Li

In [39]:
all_venues.shape

(1841, 7)

In [40]:

all_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0     Agripada              18.975302               72.824898   
1     Agripada              18.975302               72.824898   
2     Agripada              18.975302               72.824898   
3     Agripada              18.975302               72.824898   
4     Agripada              18.975302               72.824898   

                      Venue  Venue Latitude  Venue Longitude Venue Category  
0                   Celejor       18.975844        72.823679         Bakery  
1           cafe coffee day       18.976988        72.824051    Coffee Shop  
2              Baby gardens       18.973466        72.824510         Garden  
3        YMCA Swimming Pool       18.974498        72.824721           Pool  
4  YMCA Working Mens Hostel       18.973614        72.824427         Hostel

In [41]:
all_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                    
Agripada                                     5                       5      5   
Airport                                      3                       3      3   
Alaknanda                                    3                       3      3   
Ali                                          5                       5      5   
Aliganj                                      4                       4      4   
Amar Colony                                  5                       5      5   
Ambewadi                                     2                       2      2   
Anand Parbat                                 2                       2      2   
Anand Vihar                                  2                       2      2   
Andheri                                      6                       6      6   
Andheri East                                 9                       9      9   
Andheri Railway station                      6                       6      6   
Antop Hill                                   4                       4      4   
Aps Colony                                   1                       1      1   
Ashok Nagar                                  1                       1      1   
Ashok Vihar                                  1                       1      1   
Azad Nagar                                   8                       8      8   
B P t colony                                 1                       1      1   
B.P.lane                                    49                      49     49   
Badarpur                                     1                       1      1   
Bakkarwala                                   1                       1      1   
Bandra West                                 16                      16     16   
Bandra(east)                                 4                       4      4   
Bangur Nagar                                 4                       4      4   
Bank Street                                  4                       4      4   
Baroda House                                 2                       2      2   
Barwala                                      1                       1      1   
Bazar Road                                   4                       4      4   
Bazargate                                   41                      41     41   
Begumpur                                     6                       6      6   
Bengali Market                              10                      10     10   
Bhalaswa                                     1                       1      1   
Bharat Nagar                                 1                       1      1   
Bhawani Shankar                              4                       4      4   
Bhawani Shankar rd                           7                       7      7   
Birla Lines                                  2                       2      2   
Borivali                                    11                      11     11   
Central Building                             9                       9      9   
Century Mill                                 1                       1      1   
Chakala Midc                                 5                       5      5   
Chamarbaug                                   5                       5      5   
Chanakyapuri                                 1                       1      1   
Chand Nagar                                  2                       2      2   
Chand Pur                                    1                       1      1   
Chandni Chowk                               14                      14     14   
Charkop                                      4                       4      4   
Charni Road                                 15                      15     15   
Chattarpur                                   3          

In [42]:
print('There are {} uniques categories.'.format(len(all_venues['Venue Category'].unique())))

There are 218 uniques categories.


In [43]:
# one hot encoding
all_onehot = pd.get_dummies(all_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
all_onehot['Neighborhood'] = all_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [all_onehot.columns[-1]] + list(all_onehot.columns[:-1])
all_onehot = all_onehot[fixed_columns]

all_onehot.head()

Neighborhood  ATM  Accessories Store  Afghan Restaurant  Airport  \
0     Agripada    0                  0                  0        0   
1     Agripada    0                  0                  0        0   
2     Agripada    0                  0                  0        0   
3     Agripada    0                  0                  0        0   
4     Agripada    0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Arcade  Art Gallery  \
0                 0                    0             0       0            0   
1                 0                    0             0       0            0   
2                 0                    0             0       0            0   
3                 0                    0             0       0            0   
4                 0                    0             0       0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Workshop  Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0              0                0          0           0       1     0    0   
1              0                0          0           0       0     0    0   
2              0                0          0           0       0     0    0   
3              0                0          0           0       0     0    0   
4              0                0          0           0       0     0    0   

   Basketball Court  Beach  Bed & Breakfast  Beer Garden  Bengali Restaurant  \
0                 0      0                0            0                   0   
1                 0      0                0            0                   0   
2                 0      0                0            0                   0   
3                 0      0                0            0                   0   
4                 0      0                0            0                   0   

   Big Box Store  Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0              0       0           0              0          0         0   
1              0       0           0              0          0         0   
2              0       0           0              0          0         0   
3              0       0           0              0          0         0   
4              0       0           0              0          0         0   

   Bowling Alley  Breakfast Spot  Brewery  Buffet  Burger Joint  \
0              0               0        0       0             0   
1              0               0        0       0             0   
2              0               0        0       0             0   
3              0               0        0       0             0   
4              0               0        0       0             0   

   Burrito Place  Bus Station  Business Service  Cafeteria  Café  \
0              0            0                 0          0     0   
1              0            0                 0          0     0   
2              0            0                 0          0     0   
3              0            0                 0          0     0   
4              0            0                 0          0  

In [44]:
all_onehot.shape

(1841, 219)

In [45]:
all_grouped = all_onehot.groupby('Neighborhood').mean().reset_index()
all_grouped

Neighborhood       ATM  Accessories Store  Afghan Restaurant  \
0                   Agripada  0.000000           0.000000                0.0   
1                    Airport  0.000000           0.000000                0.0   
2                  Alaknanda  0.000000           0.000000                0.0   
3                        Ali  0.000000           0.000000                0.0   
4                    Aliganj  0.000000           0.000000                0.0   
5                Amar Colony  0.000000           0.000000                0.0   
6                   Ambewadi  0.000000           0.000000                0.0   
7               Anand Parbat  0.000000           0.000000                0.0   
8                Anand Vihar  0.000000           0.000000                0.0   
9                    Andheri  0.000000           0.000000                0.0   
10              Andheri East  0.000000           0.000000                0.0   
11   Andheri Railway station  0.000000           0.000000                0.0   
12                Antop Hill  0.000000           0.000000                0.0   
13                Aps Colony  0.000000           0.000000                0.0   
14               Ashok Nagar  0.000000           0.000000                0.0   
15               Ashok Vihar  0.000000           0.000000                0.0   
16                Azad Nagar  0.000000           0.000000                0.0   
17              B P t colony  0.000000           0.000000                0.0   
18                  B.P.lane  0.000000           0.000000                0.0   
19                  Badarpur  0.000000           0.000000                0.0   
20                Bakkarwala  1.000000           0.000000                0.0   
21               Bandra West  0.000000           0.000000                0.0   
22              Bandra(east)  0.000000           0.000000                0.0   
23              Bangur Nagar  0.000000           0.000000                0.0   
24               Bank Street  0.000000           0.000000                0.0   
25              Baroda House  0.000000           0.000000                0.0   
26                   Barwala  1.000000           0.000000                0.0   
27                Bazar Road  0.000000           0.000000                0.0   
28                 Bazargate  0.000000           0.000000                0.0   
29                  Begumpur  0.000000           0.000000                0.0   
30            Bengali Market  0.000000           0.000000                0.0   
31                  Bhalaswa  0.000000           0.000000                0.0   
32              Bharat Nagar  1.000000           0.000000                0.0   
33           Bhawani Shankar  0.000000           0.000000                0.0   
34        Bhawani Shankar rd  0.000000           0.000000                0.0   
35               Birla Lines  0.500000           0.000000                0.0   
36                  Borivali  0.000000           0.000000                0.0   
37          Central Building  0.000000           0.000000                0.0   
38              Century Mill  0.000000           0.000000                0.0   
39              Chakala Midc  0.000000           0.000000                0.0   
40                Chamarbaug  0.000000           0.000000                0.0   
41              Chanakyapuri  0.000000           0.000000                0.0   
42               Chand Nagar  0.500000           0.000000                0.0   
43                 Chand Pur  0.000000           0.000000                0.0   
44             Chandni Chowk  0.000000           0.000000                0.0   
45                   Charkop  0.000000           0.000000                0.0   
46               Charni Road  0.000000           0.000000                0.0   
47                Chattarpur  0.333333           0.000000                0.0   
48                Chaukhandi  0.000000           0.000000                0.0   
49              

In [46]:
num_top_venues = 5

for hood in all_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp =  all_grouped[all_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agripada----
         venue  freq
0       Hostel   0.2
1  Coffee Shop   0.2
2         Pool   0.2
3       Garden   0.2
4       Bakery   0.2


----Airport----
             venue  freq
0          Airport  0.33
1  Airport Service  0.33
2    Jewelry Store  0.33
3              ATM  0.00
4      Music Venue  0.00


----Alaknanda----
                venue  freq
0         Coffee Shop  0.33
1  Chinese Restaurant  0.33
2        Burger Joint  0.33
3                 ATM  0.00
4         Music Venue  0.00


----Ali----
               venue  freq
0              Hotel   0.2
1  Indian Restaurant   0.2
2             Hostel   0.2
3      Movie Theater   0.2
4   Asian Restaurant   0.2


----Aliganj----
               venue  freq
0  Indian Restaurant  0.50
1             Bakery  0.25
2        Record Shop  0.25
3                ATM  0.00
4             Museum  0.00


----Amar Colony----
         venue  freq
0         Food   0.2
1  Coffee Shop   0.2
2        Motel   0.2
3       Market   0.2
4         Café   0

                        venue  freq
0           Indian Restaurant   1.0
1                         ATM   0.0
2                      Museum   0.0
3           Mobile Phone Shop   0.0
4  Modern European Restaurant   0.0


----Chand Nagar----
                        venue  freq
0                         ATM   0.5
1                   Juice Bar   0.5
2                      Museum   0.0
3           Mobile Phone Shop   0.0
4  Modern European Restaurant   0.0


----Chand Pur----
                             venue  freq
0                 Business Service   1.0
1                      Music Venue   0.0
2       Modern European Restaurant   0.0
3  Molecular Gastronomy Restaurant   0.0
4              Moroccan Restaurant   0.0


----Chandni Chowk----
                           venue  freq
0              Indian Restaurant  0.29
1                    Snack Place  0.14
2                         Market  0.14
3                   Dessert Shop  0.14
4  Vegetarian / Vegan Restaurant  0.07


----Charkop----
    

                           venue  freq
0                 Ice Cream Shop  0.14
1  Vegetarian / Vegan Restaurant  0.14
2                Automotive Shop  0.14
3                      Nightclub  0.14
4            Japanese Restaurant  0.14


----Fateh Nagar----
                            venue  freq
0                            Park  0.33
1             Fried Chicken Joint  0.33
2                      Food Court  0.33
3                             ATM  0.00
4  Multicuisine Indian Restaurant  0.00


----Fatehpur Beri----
                        venue  freq
0                        Farm   1.0
1                         ATM   0.0
2                   Multiplex   0.0
3           Mobile Phone Shop   0.0
4  Modern European Restaurant   0.0


----Gandhi Nagar bazar----
                  venue  freq
0                Museum  0.25
1           Flea Market  0.25
2  Fast Food Restaurant  0.25
3          Dessert Shop  0.25
4                   ATM  0.00


----Ganeshpura----
                             venue

                venue  freq
0   Health Food Store   0.5
1  Light Rail Station   0.5
2                 ATM   0.0
3           Multiplex   0.0
4   Mobile Phone Shop   0.0


----Jama Masjid----
                venue  freq
0   Indian Restaurant  0.43
1               Hotel  0.14
2  Frozen Yogurt Shop  0.14
3              Mosque  0.14
4         Snack Place  0.14


----Janakpuri----
                  venue  freq
0        Ice Cream Shop   0.2
1     Indian Restaurant   0.2
2                  Café   0.2
3  Gym / Fitness Center   0.2
4                  Park   0.2


----Janpath----
                             venue  freq
0                             Café   1.0
1                              ATM   0.0
2                      Music Venue   0.0
3       Modern European Restaurant   0.0
4  Molecular Gastronomy Restaurant   0.0


----Janta Market----
               venue  freq
0  Indian Restaurant  0.33
1  Other Repair Shop  0.33
2          Juice Bar  0.33
3                ATM  0.00
4          Multiplex

                venue  freq
0                Park  0.25
1   Indian Restaurant  0.25
2      History Museum  0.25
3  Chinese Restaurant  0.25
4                 ATM  0.00


----Lodi Road----
                venue  freq
0                Park  0.25
1   Indian Restaurant  0.25
2      History Museum  0.25
3  Chinese Restaurant  0.25
4                 ATM  0.00


----M.P.t.----
               venue  freq
0               Café  0.22
1  Indian Restaurant  0.08
2        Coffee Shop  0.06
3   Halal Restaurant  0.06
4             Hostel  0.06


----Madanpur Khadar----
                        venue  freq
0                         ATM   1.0
1                   Multiplex   0.0
2          Miscellaneous Shop   0.0
3           Mobile Phone Shop   0.0
4  Modern European Restaurant   0.0


----Madhavbaug----
                           venue  freq
0                 Ice Cream Shop  0.25
1  Vegetarian / Vegan Restaurant  0.25
2           Fast Food Restaurant  0.25
3                   Dessert Shop  0.25
4      

                        venue  freq
0                         Bar   1.0
1                         ATM   0.0
2                   Mini Golf   0.0
3           Mobile Phone Shop   0.0
4  Modern European Restaurant   0.0


----Naigaon----
               venue  freq
0  Indian Restaurant  0.33
1       Hockey Arena  0.33
2   Department Store  0.33
3                ATM  0.00
4             Museum  0.00


----Nangal Raya----
                        venue  freq
0                         ATM   1.0
1                   Multiplex   0.0
2          Miscellaneous Shop   0.0
3           Mobile Phone Shop   0.0
4  Modern European Restaurant   0.0


----Naraina Village----
                        venue  freq
0                Dessert Shop   1.0
1                         ATM   0.0
2                      Museum   0.0
3           Mobile Phone Shop   0.0
4  Modern European Restaurant   0.0


----Nariman Point----
                venue  freq
0  Italian Restaurant  0.19
1   Indian Restaurant  0.12
2         Chaat 

                venue  freq
0               Hotel  0.25
1        Concert Hall  0.25
2         Art Gallery  0.25
3  Light Rail Station  0.25
4                 ATM  0.00


----Pragati Vihar----
                        venue  freq
0              Sandwich Place   1.0
1                         ATM   0.0
2                   Multiplex   0.0
3           Mobile Phone Shop   0.0
4  Modern European Restaurant   0.0


----Prashant Vihar----
                             venue  freq
0                      Pizza Place   0.5
1                   Clothing Store   0.5
2                      Music Venue   0.0
3       Modern European Restaurant   0.0
4  Molecular Gastronomy Restaurant   0.0


----Pratap Market----
                venue  freq
0  Light Rail Station  0.67
1       Train Station  0.33
2                 ATM  0.00
3           Multiplex  0.00
4   Mobile Phone Shop  0.00


----Punjabi Bagh----
                  venue  freq
0  Fast Food Restaurant  0.50
1                Bakery  0.25
2        Sandwic

               venue  freq
0   Department Store  0.25
1  Indian Restaurant  0.12
2      Shopping Mall  0.12
3        Coffee Shop  0.12
4     Clothing Store  0.12


----Sarita Vihar----
               venue  freq
0      Train Station   0.5
1          Juice Bar   0.5
2                ATM   0.0
3             Museum   0.0
4  Mobile Phone Shop   0.0


----Sarojini Nagar----
                  venue  freq
0     Indian Restaurant  0.43
1  Fast Food Restaurant  0.29
2           Pizza Place  0.14
3         Shopping Mall  0.14
4                   ATM  0.00


----Satbari----
                        venue  freq
0         Arts & Crafts Store   0.2
1                      Resort   0.2
2                        Farm   0.2
3  Construction & Landscaping   0.2
4                       Hotel   0.2


----Secretariat North----
                        venue  freq
0               Metro Station   1.0
1                         ATM   0.0
2                   Multiplex   0.0
3           Mobile Phone Shop   0.0
4  Mod

                        venue  freq
0                  Restaurant   0.5
1          Seafood Restaurant   0.5
2                         ATM   0.0
3           Mobile Phone Shop   0.0
4  Modern European Restaurant   0.0


----Vasant Kunj----
                        venue  freq
0              Ice Cream Shop  0.33
1                Burger Joint  0.33
2                        Café  0.33
3                      Museum  0.00
4  Modern European Restaurant  0.00


----Vasant Kunj pkt-A----
                        venue  freq
0              Ice Cream Shop  0.33
1                Burger Joint  0.33
2                        Café  0.33
3                      Museum  0.00
4  Modern European Restaurant  0.00


----Vasant Vihar-1----
                        venue  freq
0           Indian Restaurant   0.5
1           Convenience Store   0.5
2                         ATM   0.0
3                      Museum   0.0
4  Modern European Restaurant   0.0


----Vasant Vihar-2----
                        venue  freq


In [49]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [50]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = all_grouped['Neighborhood']

for ind in np.arange(all_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(all_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0     Agripada           Coffee Shop                Bakery   
1      Airport               Airport       Airport Service   
2    Alaknanda           Coffee Shop    Chinese Restaurant   
3          Ali                 Hotel      Asian Restaurant   
4      Aliganj     Indian Restaurant                Bakery   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                Garden                  Pool                Hostel   
1         Jewelry Store           Yoga Studio            Donut Shop   
2          Burger Joint           Yoga Studio            Donut Shop   
3     Indian Restaurant         Movie Theater                Hostel   
4           Record Shop           Yoga Studio            Donut Shop   

  6th Most Common Venue       7th Most Common Venue 8th Most Common Venue  \
0    Airport Food Court                Airport Gate           Flower Shop   
1           Flower Shop                 Flea Market     Fish & Chips Shop   
2           Flea Market           Fish & Chips Shop                 Field   
3    Airport Food Court  Construction & Landscaping                  Food   
4           Flea Market           Fish & Chips Shop                 Field   

  9th Most Common Venue 10th Most Common Venue  
0           Flea Market      Fish & Chips Shop  
1                 Field   Fast Food Restaurant  
2  Fast Food Restaurant         Farmers Market  
3           Flower Shop            Flea Market  
4  Fast Food Restaurant         Farmers Market

In [51]:
# set number of clusters
kclusters = 5

all_grouped_clustering = all_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(all_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([2, 2, 2, 2, 0, 2, 0, 3, 2, 3, 2, 3, 2, 0, 2, 2, 2, 2, 2, 2, 4, 2,
       2, 2, 2, 0, 4, 3, 2, 2, 2, 2, 4, 2, 2, 4, 2, 2, 2, 3, 2, 0, 4, 2,
       0, 2, 2, 2, 2, 3, 2, 0, 3, 2, 2, 2, 2, 2, 2, 2, 3, 2, 2, 2, 2, 2,
       2, 2, 2, 2, 2, 2, 2, 3, 3, 2, 3, 2, 2, 2, 2, 2, 2, 2, 3, 4, 2, 2,
       2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 1, 2, 2, 0, 2, 2, 2, 0,
       2, 2, 2, 2, 2, 2, 2, 0, 2, 2, 2, 2, 0, 2, 2, 0, 2, 4, 1, 3, 2, 2,
       4, 2, 0, 2, 2, 2, 2, 2, 2, 4, 2, 2, 2, 2, 2, 0, 2, 2, 0, 2, 1, 2,
       3, 2, 2, 2, 2, 2, 2, 2, 2, 2, 4, 3, 2, 2, 2, 2, 2, 2, 2, 2, 0, 2,
       2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 4, 2, 2, 2, 2, 2, 2,
       2, 2, 3, 2, 0, 4, 2, 2, 3, 4, 2, 2, 2, 2, 2, 2, 2, 4, 2, 2, 2, 2,
       2, 0, 2, 2, 2, 2, 2, 2, 2, 2, 0, 2, 2, 2, 2, 2, 2, 2, 0, 0, 2, 2,
       3, 2, 2, 3, 3, 2, 3, 0, 0, 3, 1, 2, 0, 3, 2, 2, 2, 0, 2, 2, 2, 2,
       2, 2, 2, 2, 3, 2, 0, 2, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 0, 2, 1, 2,
       2, 2, 2, 2, 2, 2, 1, 2, 2, 2, 2, 2, 0, 2, 2,

In [52]:
kmeans.labels_.shape

(332,)

In [53]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels',kmeans.labels_)

In [54]:
all_merged =data
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
all_merged = all_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
all_merged.head() # check the last columns!

Latitude  Longitude  Neighborhood  Cluster Labels 1st Most Common Venue  \
3  18.975302  72.824898      Agripada             2.0           Coffee Shop   
4  19.090201  72.863808       Airport             2.0               Airport   
5  19.186776  72.859313      Ambewadi             0.0         Women's Store   
6  19.119698  72.846420       Andheri             3.0  Fast Food Restaurant   
7  19.115883  72.854202  Andheri East             2.0     Indian Restaurant   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
3                Bakery                Garden                  Pool   
4       Airport Service         Jewelry Store           Yoga Studio   
5     Indian Restaurant            Donut Shop           Flower Shop   
6            Food Court     Indian Restaurant                Bakery   
7                 Hotel         Shopping Mall    Light Rail Station   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3                Hostel    Airport Food Court          Airport Gate   
4            Donut Shop           Flower Shop           Flea Market   
5           Flea Market     Fish & Chips Shop                 Field   
6            Restaurant           Yoga Studio            Donut Shop   
7     Electronics Store          Camera Store            Smoke Shop   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
3           Flower Shop           Flea Market      Fish & Chips Shop  
4     Fish & Chips Shop                 Field   Fast Food Restaurant  
5  Fast Food Restaurant        Farmers Market                   Farm  
6     Fish & Chips Shop                 Field         Farmers Market  
7    Chinese Restaurant        Cricket Ground            Event Space

In [55]:
all_merged['Cluster Labels'].count()

336

In [56]:

all_merged.dropna(inplace=True)
all_merged.shape

(336, 14)

In [57]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(all_merged['Latitude'],all_merged['Longitude'], all_merged['Neighborhood'], all_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [66]:
all_merged.loc[all_merged['Cluster Labels'] == 0, all_merged.columns[[1] + list(range(4, all_merged.shape[1]))]]

Longitude 1st Most Common Venue 2nd Most Common Venue  \
5    72.859313         Women's Store     Indian Restaurant   
34   72.837053     Indian Restaurant           Flea Market   
65   72.830243     Indian Restaurant            Food Truck   
72   72.834717     Indian Restaurant            Hookah Bar   
78   72.827938     Indian Restaurant  Fast Food Restaurant   
102  72.856318     Indian Restaurant           Yoga Studio   
122  72.847871          Hockey Arena     Indian Restaurant   
139  72.838343     Indian Restaurant                Bakery   
46   77.290564     Indian Restaurant      Department Store   
80   77.116060     Indian Restaurant            Food Truck   
83   77.286902     Other Repair Shop     Indian Restaurant   
104  77.093102     Indian Restaurant         Train Station   
125  77.219843     Indian Restaurant                Bakery   
154  77.232395           Men's Store     Indian Restaurant   
170  77.271450     Indian Restaurant                  Café   
196  77.232194     Indian Restaurant           Snack Place   
215  77.120690     Convenience Store     Indian Restaurant   
224  77.230552              Pharmacy     Indian Restaurant   
237  77.230853                Market     Indian Restaurant   
242  77.232961     Indian Restaurant                 Hotel   
254  77.230690     Indian Restaurant                  Park   
369  77.136585     Indian Restaurant           Yoga Studio   
380  77.188521     Indian Restaurant           Yoga Studio   
422  77.204595     Indian Restaurant    Airport Food Court   
459  77.179799     Indian Restaurant                Market   
462  77.179122     Indian Restaurant                   ATM   
474  77.099592     Indian Restaurant           Yoga Studio   
476  77.195370     Indian Restaurant  Fast Food Restaurant   
480  77.163590      Business Service     Indian Restaurant   
491  77.160791     Convenience Store     Indian Restaurant   
492  77.160791     Convenience Store     Indian Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
5              Donut Shop           Flower Shop           Flea Market   
34            Pizza Place                  Café        Discount Store   
65            Cheese Shop                Market           Yoga Studio   
72                 Bakery           Yoga Studio            Donut Shop   
78            Yoga Studio        Discount Store           Flea Market   
102        Discount Store           Flea Market     Fish & Chips Shop   
122      Department Store           Yoga Studio            Donut Shop   
139    Chinese Restaurant            Playground                  Café   
46            Yoga Studio            Donut Shop           Flea Market   
80         Cosmetics Shop    Salon / Barbershop  Gym / Fitness Center   
83              Juice Bar           Yoga Studio        Discount Store   
104           Yoga Studio        Discount Store           Flea Market   
125           Record Shop           Yoga Studio            Donut Shop   
154  Gym / Fitness Center           Yoga Studio            Donut Shop   
170           Yoga Studio        Discount Store           Flea Market   
196                Market          Dessert Shop              Pharmacy   
215                Bakery           Yoga Studio            Donut Shop   
224           Yoga Studio        Discount Store           Flea Market   
237           Yoga Studio            Donut Shop           Flea Market   
242    Frozen Yogurt Shop                Mosque           Snack Place   
254    Chinese Restaurant     Food & Drink Shop            Restaurant   
369        Discount Store           Flea Market     Fish & Chips Shop   
380        Discount Store           Flea Market     Fish & Chips Shop   
422            Restaurant                  Café           Snack Place   
459                Bakery           Yoga Studio        Duty-free Shop   
462                Market            Donut Shop           Flea Market   
474        Discount Store           Flea Market  

In [70]:
all_merged.loc[all_merged['Cluster Labels'] == 1, all_merged.columns[[1] + list(range(4, all_merged.shape[1]))]]

Longitude 1st Most Common Venue 2nd Most Common Venue  \
23   77.312395         Metro Station             Cafeteria   
245  77.213691         Metro Station            Donut Shop   
259  77.211989         Metro Station            Donut Shop   
266  77.212282         Metro Station            Donut Shop   
267  77.214397         Metro Station            Donut Shop   
296  77.149403         Metro Station            Donut Shop   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
23            Yoga Studio            Donut Shop           Flea Market   
245           Flower Shop           Flea Market     Fish & Chips Shop   
259           Flower Shop           Flea Market     Fish & Chips Shop   
266           Flower Shop           Flea Market     Fish & Chips Shop   
267           Flower Shop           Flea Market     Fish & Chips Shop   
296           Flower Shop           Flea Market     Fish & Chips Shop   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
23      Fish & Chips Shop                 Field  Fast Food Restaurant   
245                 Field  Fast Food Restaurant        Farmers Market   
259                 Field  Fast Food Restaurant        Farmers Market   
266                 Field  Fast Food Restaurant        Farmers Market   
267                 Field  Fast Food Restaurant        Farmers Market   
296                 Field  Fast Food Restaurant        Farmers Market   

    9th Most Common Venue 10th Most Common Venue  
23         Farmers Market                   Farm  
245                  Farm     Falafel Restaurant  
259                  Farm     Falafel Restaurant  
266                  Farm     Falafel Restaurant  
267                  Farm     Falafel Restaurant  
296                  Farm     Falafel Restaurant

In [71]:
all_merged.loc[all_merged['Cluster Labels'] == 2, all_merged.columns[[1] + list(range(4, all_merged.shape[1]))]]

Longitude       1st Most Common Venue          2nd Most Common Venue  \
3     72.824898                 Coffee Shop                         Bakery   
4     72.863808                     Airport                Airport Service   
7     72.854202           Indian Restaurant                          Hotel   
9     72.865256           Indian Restaurant                          Trail   
11    72.840038                        Park              Indian Restaurant   
12    72.861599                    Tea Room                    Yoga Studio   
14   100.340014                        Café              Indian Restaurant   
15    72.830267                        Café              Indian Restaurant   
16    72.849811                 Pizza Place             Chinese Restaurant   
17    72.833678                  Food Truck                      Bookstore   
18    72.832264           Indian Restaurant           Fast Food Restaurant   
21    72.837370               Shopping Mall                 Clothing Store   
22    72.840432               Women's Store                  Movie Theater   
23    72.857363                    Platform                   Burger Joint   
27    72.835335           Indian Restaurant                    Coffee Shop   
28    72.825565                 Karaoke Bar                 Discount Store   
30    72.840800           Indian Restaurant                       Pharmacy   
31    72.825865           Indian Restaurant                           Bank   
32    72.817440                   Juice Bar                Harbor / Marina   
36    72.827340               Train Station      College Academic Building   
37    72.825969                 Men's Store              Indian Restaurant   
38    72.845762                       Plaza                  Train Station   
39    72.806538                 Yoga Studio                         Bakery   
42    72.839427           Indian Restaurant           Fast Food Restaurant   
43    72.859621                        Café                  Train Station   
45    72.825031                        Café       Mediterranean Restaurant   
46    72.860493                  Food Truck               Department Store   
47    72.831012                 Coffee Shop             Seafood Restaurant   
50    72.844548         Government Building                         Garden   
51    72.809547              Sandwich Place                         Bakery   
52    72.820791                  Board Shop                Automotive Shop   
53    72.817908           Indian Restaurant                      Juice Bar   
54    72.835284           Convenience Store                    Yoga Studio   
55    72.850018           Indian Restaurant                    Snack Place   
58    72.832030           Indian Restaurant                    Coffee Shop   
59    72.810098                Concert Hall              Indian Restaurant   
60    72.813573           Indian Restaurant                          Hotel   
63    72.832289                 Coffee Shop                    Pizza Place   
70    72.863808                     Airport                Airport Service   
71    72.835335           Indian Restaurant                    Coffee Shop   
73    72.826786           Indian Restaurant                         Bakery   
75    72.837382            Indoor Play Area                   Cocktail Bar   
76    72.827528                        Café                         Lounge   
79    72.826435                  Donut Shop                     Shoe Store   
80    72.864084        Fast Food Restaurant             Seafood Restaurant   
81    72.842227                        Food                         Market   
83    72.874835                  Kids Store                    Yoga Studio   
87    72.844873                      Tunnel          General Entertainment   
88    72.852981                 Flower Shop                            Gym   
91    72.841534                 Men's Store                 Ice Cream Shop   
93   100.340014             

In [74]:
all_merged.loc[all_merged['Cluster Labels'] == 3, all_merged.columns[[1] + list(range(4, all_merged.shape[1]))]]

Longitude           1st Most Common Venue          2nd Most Common Venue  \
6    72.846420            Fast Food Restaurant                     Food Court   
8    72.846420            Fast Food Restaurant                     Food Court   
29   72.861808                           Hotel           Fast Food Restaurant   
35   72.832672  Multicuisine Indian Restaurant           Fast Food Restaurant   
41   72.842876            Fast Food Restaurant                    Flower Shop   
74   72.864942            Gym / Fitness Center           Fast Food Restaurant   
95   72.827395                  Ice Cream Shop  Vegetarian / Vegan Restaurant   
120  72.852750                             Bar              Indian Restaurant   
143  72.839201                     Pizza Place              Indian Restaurant   
162  72.820498            Fast Food Restaurant                         Castle   
9    77.321516            Fast Food Restaurant                    Pizza Place   
13   77.235436                     Flea Market           Fast Food Restaurant   
31   77.290185            Fast Food Restaurant                    Yoga Studio   
62   77.030036                     Pizza Place              Indian Restaurant   
105  77.132461            Fast Food Restaurant                         Bakery   
106  77.132461            Fast Food Restaurant                         Bakery   
107  77.107864                  Sandwich Place                    Yoga Studio   
115  77.096496            Fast Food Restaurant              Indian Restaurant   
116  77.096496            Fast Food Restaurant              Indian Restaurant   
172  77.341374                  Sandwich Place                    Yoga Studio   
197  77.229438                     Snack Place           Fast Food Restaurant   
221  77.180140            Fast Food Restaurant           Kitchen Supply Store   
232  77.223248                   Metro Station                     Food Court   
377  77.235436                     Flea Market           Fast Food Restaurant   
389  76.866448            Fast Food Restaurant                    Yoga Studio   
447  77.193445                     Snack Place              Indian Restaurant   
458  77.184701                           Hotel                 History Museum   
466  77.184701                           Hotel                 History Museum   

             3rd Most Common Venue 4th Most Common Venue  \
6                Indian Restaurant                Bakery   
8                Indian Restaurant                Bakery   
29                            Café        Discount Store   
35                        Platform         Train Station   
41   Vegetarian / Vegan Restaurant        Breakfast Spot   
74                       BBQ Joint           Yoga Studio   
95            Fast Food Restaurant          Dessert Shop   
120           Fast Food Restaurant           Yoga Studio   
143           Fast Food Restaurant          Dessert Shop   
162                  Train Station         Movie Theater   
9                Indian Restaurant    Light Rail Station   
13                    Dessert Shop                Museum   
31                      Donut Shop           Flower Shop   
62            Fast Food Restaurant           Yoga Studio   
105                 Sandwich Place           Yoga Studio   
106                 Sandwich Place           Yoga Studio   
107                 Discount Store     Fish & Chips Shop   
115                  Women's Store                  Café   
116                  Women's Store                  Café   
172                 Discount Store     Fish & Chips Shop   
197                 Hardware Store    Light Rail Station   
221                    Yoga Studio            Donut Shop   
232                           Bank  Fast Food Restaurant   
377                   Dessert Shop                Museum   
389                     Donut Shop           Flower Shop   
447           Fast Food Restaurant           Yoga Studio   
458           Fast Food Restaurant 

In [73]:
all_merged.loc[all_merged['Cluster Labels'] == 4, all_merged.columns[[1] + list(range(4, all_merged.shape[1]))]]

Longitude 1st Most Common Venue 2nd Most Common Venue  \
20   72.856474                   ATM            Donut Shop   
65   77.312267                   ATM             Juice Bar   
70   77.019182                   ATM            Donut Shop   
71   77.097591                   ATM             Juice Bar   
87   77.105571                   ATM           Pizza Place   
149  77.046691                   ATM                  Café   
161  77.300518                   ATM            Donut Shop   
193  77.197626                   ATM        Ice Cream Shop   
281  77.061882                   ATM            Donut Shop   
291  77.163475                   ATM          Burger Joint   
318  77.193991                   ATM     Convenience Store   
327  77.174137                   ATM            Donut Shop   
418  77.082305                   ATM              Pharmacy   
443  77.110335                   ATM            Donut Shop   
448  77.201496                   ATM            Donut Shop   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
20            Flower Shop           Flea Market     Fish & Chips Shop   
65         Discount Store           Flea Market     Fish & Chips Shop   
70            Flower Shop           Flea Market     Fish & Chips Shop   
71         Discount Store           Flea Market     Fish & Chips Shop   
87                  Diner     Fish & Chips Shop                 Field   
149        Discount Store           Flea Market     Fish & Chips Shop   
161           Flower Shop           Flea Market     Fish & Chips Shop   
193        Discount Store           Flea Market     Fish & Chips Shop   
281           Flower Shop           Flea Market     Fish & Chips Shop   
291            Donut Shop           Flea Market     Fish & Chips Shop   
318            Donut Shop           Flower Shop           Flea Market   
327           Flower Shop           Flea Market     Fish & Chips Shop   
418                 Hotel            Whisky Bar           Flower Shop   
443           Flower Shop           Flea Market     Fish & Chips Shop   
448           Flower Shop           Flea Market     Fish & Chips Shop   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
20                  Field  Fast Food Restaurant        Farmers Market   
65                  Field  Fast Food Restaurant        Farmers Market   
70                  Field  Fast Food Restaurant        Farmers Market   
71                  Field  Fast Food Restaurant        Farmers Market   
87   Fast Food Restaurant        Farmers Market                  Farm   
149                 Field  Fast Food Restaurant        Farmers Market   
161                 Field  Fast Food Restaurant        Farmers Market   
193                 Field  Fast Food Restaurant        Farmers Market   
281                 Field  Fast Food Restaurant        Farmers Market   
291                 Field  Fast Food Restaurant        Farmers Market   
318     Fish & Chips Shop                 Field  Fast Food Restaurant   
327                 Field  Fast Food Restaurant        Farmers Market   
418     Fish & Chips Shop                 Field  Fast Food Restaurant   
443                 Field  Fast Food Restaurant        Farmers Market   
448                 Field  Fast Food Restaurant        Farmers Market   

    9th Most Common Venue 10th Most Common Venue  
20                   Farm     Falafel Restaurant  
65                   Farm     Falafel Restaurant  
70                   Farm     Falafel Restaurant  
71                   Farm     Falafel Restaurant  
87     Falafel Restaurant            Event Space  
149                  Farm     Falafel Restaurant  
161                  Farm     Falafel Restaurant  
193                  Farm     Falafel Restaurant  
281                  Farm     Falafel Restaurant  
291                  Farm     Falafel Restaurant  
318        Farmers Market                   Farm  
327                  Farm     Falafel Restaurant  
418        